# **Portfolio Project:** Web Scraping Using BeautifulSoup
# **Rob Boswell**

---
---

### This portfolio project shows how to create a web crawler using the BeautifulSoup Python library. I demonstrate how to combine BeautifulSoup with a TOR-based library to enable anonymous web scraping.

<br>

### In this project, I will be scraping a user-defined list of URLs for the embedded URL links within them, the html text on those URLs, and any tables which might also exist on the scraped URLs.

<br>

### Specifically, I will be creating a Pandas DataFrame with 4 columns. The first will contain the original URLs from the user-defined list from which the embedded links within them are scraped. The second will contain the actual URLs that are embedded and scraped. The third will contain the scraped text from the embedded URLs. Lastly, the forth will contain the html code for any tables which exist on the embedded URLs.

<br>

### I will then take the resulting Pandas DataFrame and use display options and pandas styling to visualize the first three columns. Afterward, I will show how the scraped tables can be viewed using IPython.display.

<br>

### There are many design options for web scrapers depending on specific goals; for instance, this code could be adapted to scrape PDF files, meta data, or images instead of HTML text.

---

## **BeautifulSoup Web Scraper Implementation:**

---

### *Data Cleaning:*

### - As discussed in greater detail in the comments in the code below, I use Regular Expression (regex) to clean scraped text. I make sure that common forms of punctuation are kept in the text, and keep alphanumeric characters, but I remove special characters and newline characters. Removing newline characters (which appear as \n) means that paraphraphs of text from a single HTML document will be concatenated together in your output display. I do not use regex to clean scraped tables, as doing so would remove the HTML code necessary to visualize them in table format. 

<br>

### *Final Format:*

### - I keep all originating URLs, scraped embedded URLs, scraped text, and HTML tables in the same output Pandas DataFrame. However, it would be easy for a user to create separate Pandas DataFrames for each unique originating URL in the user-defined URL list if they chose to do so, by subsetting the output DataFrame.

In [ ]:
!pip install torpy -U
!pip install pandas
!pip install bs4
!pip install html5lib

In [1]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd
import time 
from urllib.parse import urljoin
from io import StringIO 

In [1]:
# Optional function to use to check your IP address before using TOR to compare with the TOR IP address to ensure TOR is working
def check_ip():
    try:
        response = requests.get('https://ifconfig.me', timeout=10)
        print("Current IP:", response.text.strip())
    except Exception as e:
        print(f"Failed to check IP address: {e}")

In [2]:
def init():
    # Optional: Check IP before using Tor
    # print("IP before Tor:")
    # check_ip()

    from torpy import TorClient
    hostname = 'ifconfig.me'  # It's possible use onion hostname here as well
    with TorClient() as tor:
        # Choose random guard node and create 3-hops circuit
        with tor.create_circuit(3) as circuit:
            # Create tor stream to host
            with circuit.create_stream((hostname, 80)) as stream:
                # Now we can communicate with host
                stream.send(b'GET / HTTP/1.0\r\nHost: %s\r\n\r\n' % hostname.encode())
                recv = stream.recv(1024)
                print("IP Used by Tor:", recv.decode().strip())
    
    return 0

## Below is the main regex term I will use to clean the web scraped text, and an explanation of each component:

#### **Note:** The | (before each subsequent term) in regex functions serves as a logical OR operator. It allows you to match any one of multiple patterns separated by the |. It means "if the previous pattern does not match, see if the next pattern does."

### tmp_text = re.sub(
###                       ```r"[^A-Za-z0-9,;:.()?\s…'’%$\-\"“”—]+"```
###                        ```r"|(?<!\d)\%"```
###                        ```r"|\$(?!\d)"```
###                        ```r"|(?<![A-Za-z\s])-|-(?![A-Za-z\s])"```
###                        ```r"|(?<!\w)['’\"“”](?!\w)"```,
###                        ' ',
###                        tmp_text
###                    )

---
---

### **Breakdown:**
### **```[^A-Za-z0-9,;:.()?\s…'’%$\-\"“”—]+```**

#### • ```[^ ]```: This denotes a negated character class, which matches any character not listed inside the brackets.
#### • ```A-Za-z0-9```: Matches any uppercase letter (A-Z), lowercase letter (a-z), or digit (0-9).
#### • ```,;:.()?```: Matches the punctuation characters comma, semicolon, colon, period, parentheses, and question mark.
#### • ```\s```: Matches any whitespace character (space, tab, newline, etc.).
#### • ```…```: Matches the ellipsis character.
#### • ```'’```: Matches both straight and curly apostrophes/single quotes.
#### • ```%$-```: Matches the percent sign %, dollar sign $, and hyphen -.
#### • ```\"“”```: Matches straight double quotes ", curly left double quote “, and curly right double quote ”.
#### • ```—```: Matches em dashes.
#### • ```+```: Matches one or more of the preceding elements (inside the square brackets). This part effectively removes any sequence of characters that do not match the specified characters.
<u>Purpose:</u> This ensures athat all characters represented inside the square brackets will be retained in the scraped text.

---

### **```(?<!\d)\%```**

#### • ```\%```: Matches the percent sign character.
#### • ```(?<!\d)```: An assertion that checks if the character <u>immediately preceding</u> the `%` is not a digit. If this condition is true, it will match the `%` sign and allow you to remove it.
<u>Purpose:</u> This ensures that only `%` signs directly associated with numeric percentages (like "50%") are retained.

---

### **```\$(?!\d)```**

#### • ```\$```: Matches the dollar sign character.
#### • ```(?!\d)```: An assertion that checks if the character <u>immediately following</u> the `$` is not a digit. If this condition is true, it will match the `$` sign and allow you to remove it.
<u>Purpose:</u> This ensures that only `$` signs directly associated with numeric amounts (like "$100") are retained.

---

### **```(?<![A-Za-z\s])-|-(?![A-Za-z\s])```** 
#### Note: The | denotes these are two combined terms, discussed below

#### • ```(?<![A-Za-z\s])-```: An assertion that matches a ***hyphen - if it <u>is not preceded by</u> a letter or a space.***

#### • ```-(?![A-Za-z\s])```: An assertion that matches a ***hyphen - if it <u>is not followed by</u> a letter or a space.***
<u>Purpose:</u> This removes hyphens that are not part of hyphenated words, or not part of sentences where there is a space on one side of a hyphen, such as in "Short- and long-term goals are important."

---

### **```(?<!\w)['’\"“”](?!\w)```**

#### • ```['’\"“”]```: Matches either a straight `'` or curly `’` single quote/apostrophe, or a straight or curly double quotation.
#### • ```(?<!\w)```: An assertion that matches a ***quote or apostrophe if it <u>is not preceded by</u> a word character*** (letters, digits, or underscore).
#### • ```(?!\w)```: An assertion that matches a ***quote or apostrophe if it <u>is not followed by</u> a word character.***
<u>Purpose:</u> This allows you to remove single or double quotes or apostrophes that are not part of a word or contraction.

---
---

In [33]:
# The following code uses the threading library, which can help prevent the scraper from hanging indefinitely 
# on a single request. 

import threading

# fetch_url performs an HTTP GET request to fetch a URL using a requests.Session object. 
# The result of the request (either a response or an exception) is stored in a result list at the specified index.

# Thread Role: This function encapsulates the logic that will be run concurrently in a thread, isolating the network 
# operation to prevent blocking the main execution flow.

def fetch_url(session, url, result, index, timeout_duration):
    try:
        response = session.get(url, timeout=timeout_duration)
        result[index] = response
    except Exception as e:
        result[index] = e

from bs4 import BeautifulSoup
import re
        
def my_scraper(tmp_url_in, scrape_timeout=40):
    tmp_text = ''
    max_retries = 3
    attempt = 0
    scraped_tables_html = ''
    response = None  # Initialize response to None

    while attempt <= max_retries:
        session = requests.Session()
        session.max_redirects = 3

        # Use a list to store the response or exception
        result = [None]

        # Start a thread to fetch the URL
        # This line creates a new Thread object. The target argument specifies the function to run in the new 
        # thread (fetch_url), and args provides the arguments to pass to this function when it starts. 
        
        # 0: Specifies the index in the result list where the response will be stored, allowing the main thread 
        # to access the result after the thread completes.
        
        thread = threading.Thread(target=fetch_url, args=(session, tmp_url_in, result, 0, scrape_timeout))
        thread.start() # Executes the thread, allowing the fetch_url function to run concurrently with the main program.
        thread.join(timeout=scrape_timeout) # Waits for the thread to complete its task, up to a specified timeout

        if thread.is_alive(): #  Checks if thread is still running after the timeout specified in the join() call has elapsed.
            print(f"Scraping timed out for {tmp_url_in}. Moving to next URL.")
            thread.join()  # Ensures thread is properly joined, then terminated (to prevent hanging), and cleans up resources.
            attempt += 1
            time.sleep(5)
            continue  # Retry in case of a timeout

        # Get the response from the result
        response = result[0]

        if isinstance(response, requests.Response):
            if response.status_code == 200:
                if 'text/html' in response.headers.get('Content-Type', ''):
                    soup = BeautifulSoup(response.text, 'html.parser')
                    
                    # Revised line to strip HTML tags
                    tmp_text = ' '.join(p.get_text() for p in soup.find_all('p')).replace('\n', ' ')
                    
                    # Decode the text to process escape sequences. If you do not use this line, backshlahses may only be hidden and not removed.
                    # To ensure that the backslashes are actually removed, first explicitly decode the string characters so backslashes will be 
                    # visible.
                    tmp_text = tmp_text.encode('unicode_escape').decode('unicode_escape')
                    
                    tmp_text = re.sub(
                        r"[^A-Za-z0-9,;:.()?\s…'’%$\-\"“”—]+"  # Match unwanted characters
                        r"|(?<!\d)\%"  # Remove standalone percent signs not preceded by a digit
                        r"|\$(?!\d)"  # Remove standalone dollar signs not followed by a digit
                        r"|(?<![A-Za-z\s])-|-(?![A-Za-z\s])"  # Handle hyphens in certain contexts
                        r"|(?<!\w)['’\"“”](?!\w)",  # Handle quotes in certain contexts
                        ' ',
                        tmp_text
                    )
                                           
                    # Replace any sequence of multiple whitespace characters (spaces, tabs, newlines, etc.) with a single 
                    # space and then trim leading and trailing whitespace from the string.
                    tmp_text = re.sub(r'\s+', ' ', tmp_text).strip()
                    
                    if soup.find('table'):
                        tables_html = [str(table) for table in soup.find_all('table')]
                        scraped_tables_html = ''.join(tables_html)
                        result_message = "Scraped text and tables"
                    else:
                        result_message = "Scraped text only"
                    
                    print(f"{result_message}: {tmp_url_in}")
                    break  # Successfully scraped, exit the loop
                else:
                    print(f"Non-HTML content type for {tmp_url_in}: {response.headers.get('Content-Type')}")
                    break
            else:
                print(f"Failed to scrape {tmp_url_in}: Status code {response.status_code}")
                break

        elif isinstance(response, requests.exceptions.RequestException):
            print(f"Failed to scrape {tmp_url_in}: {response}")
            break  # Unsuccessful connection, exit the loop

    if response is None:
        # If no response was ever received, indicate this explicitly
        print(f"Failed to scrape {tmp_url_in}: No response received.")

    return tmp_text, scraped_tables_html



In [89]:
def fetch_urls(user_urls):
    from bs4 import BeautifulSoup
    import re

    all_urls = []

    for url in user_urls:
        try:
            response = requests.get(url, timeout=30)
            soup = BeautifulSoup(response.text, "html.parser")
            for link in soup.find_all('a', href=True):
                full_url = urljoin(url, link['href'])
                all_urls.append((url, full_url))
        except Exception as e:
            print(f"Failed to fetch URLs from {url}: {e}")
            continue

    all_urls = list(set(all_urls)) # Remove any potential duplicate URLs
    return all_urls



In [90]:
def write_crawl_results(user_urls):
    import re
    import pandas as pd
    tmp_pd = pd.DataFrame(columns=['original_url', 'scraped_url', 'scraped_text', 'scraped_tables'])

    init()

    all_urls = fetch_urls(user_urls)

    for original_url, scraped_url in all_urls:
        if not scraped_url.startswith(('http://', 'https://')):
            scraped_url = urljoin(original_url, scraped_url)
        scraped_text, scraped_tables = my_scraper(scraped_url)
        if scraped_text or scraped_tables:
            try:
                tmp_pd = pd.concat([tmp_pd, pd.DataFrame({
                    'original_url': [original_url],
                    'scraped_url': [scraped_url],
                    'scraped_text': [scraped_text],
                    'scraped_tables': [scraped_tables]
                })], ignore_index=True)
    
            except Exception as e:
                print(f"Failed to append data for {scraped_url}: {e}")
                pass

    return tmp_pd



In [96]:
user_provided_urls = [
    'https://en.wikipedia.org/wiki/Web_scraping',
    'https://en.wikipedia.org/wiki/Data_scraping',
    
    # Add more URLs as needed
]

final_data = write_crawl_results(user_provided_urls)

IP Used by Tor: HTTP/1.0 200 OK
date: Sat, 17 Aug 2024 15:28:16 GMT
content-type: text/plain
Content-Length: 14
access-control-allow-origin: *
via: 1.1 google

107.189.10.175
Scraped text and tables: https://en.wikipedia.org/wiki/Facebook,_Inc._v._Power_Ventures,_Inc.
Scraped text and tables: https://en.wikipedia.org/wiki/Reuters
Scraped text only: https://en.wikipedia.org/wiki/Wrapper_(data_mining)
Scraped text and tables: https://en.wikipedia.org/wiki/Web_scraping#See_also
Scraped text and tables: https://en.wikipedia.org/wiki/Web_scraping#cite_ref-21
Scraped text and tables: https://en.wikipedia.org/wiki/Web_scraping
Scraped text and tables: https://en.wikipedia.org/wiki/Web_scraping#References
Scraped text only: https://en.wikipedia.org/w/index.php?title=Data_scraping&action=edit
Scraped text and tables: https://en.wikipedia.org/wiki/Data_scraping#cite_ref-3
Scraped text and tables: https://en.wikipedia.org/wiki/Data_structures
Scraped text and tables: https://en.wikipedia.org/wiki

In [97]:
final_data['scraped_text'] = final_data['scraped_text'].str.strip()
final_data = final_data[final_data['scraped_text'] != '']

In [98]:
# Reset the indexes first to ensure the indexes correctly reflect the row positions.
final_data.reset_index(drop=True, inplace=True)

In [2]:
# Save the object containing the scraped data so that you do not need to re-scrape the same data in the future.
import pickle

# pickle.dump(final_data, open('final_data.pkl', 'wb'))
# final_data = pickle.load(open('final_data.pkl', 'rb'))

---
---

### **Visualizing the Scraped Text - An Initial Approach:**

---

### First, I will show you code you technically could use to display the entire Pandas DataFrame. However, the font-styling and text structure in the output would not look very pretty. 

### Additionally, I do not recommend using this code if you are using a web browser-based Python IDE like Jupyter Notebook because the following error can occur due to high data rate restrictions if you have scraped a lot of web pages like I have. I.e., use this code only if you are using a non-browser-based IDE (e.g., Visual Studio Code or Spyder). Further below, I will show you better options for displaying your scraped data.

In [12]:
import pandas as pd

pd.set_option('display.max_rows', None) # Print all rows. If this line is not used, only the first and last 5 rows will be shown 
pd.set_option('display.max_colwidth', None) # Prevent column width truncation

print(final_data[["original_url", "scraped_url", "scraped_text"]]) # Running the code in print() will hide any escape characters

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



---

### **A Better Approach to Visualizing Scraped Text Data:**

---

### The following display code allows you to scroll down through all of the scraped text from the embedded URLs.

### It also provides the extra text cleaning steps of 1) removing escape characters that could otherwise appear in the display, and 2) preventing the misinterpretation of characters like `$` signs that could otherwise alter the font styling in the display.

### You can either read the scraped text directly from the display that the code below creates by scrolling down, or you can find a specific scraped web page of interest in the display, and then extract that specific page using code I will show you further below.


In [7]:
from IPython.display import display, HTML
import html
import pandas as pd

# Print all rows. If this line is not used, only the first and last 5 rows will be shown 
pd.set_option('display.max_rows', None)
# Set the maximum column width to None to prevent truncation
pd.set_option('display.max_colwidth', None)

from html import unescape

# Explanation of the wrap_in_pre() function:

# 1) I use the unescape() function from the html module in wrap_in_pre() to unescape any previously escaped HTML entities 
# in the text. This step gracefully handles backslahes. E.g., it ensures any backslash followed by an apostrophe (\') is 
# correctly converted back to a simple apostrophe (').

# 2) The <pre> tags ensure all text within them is treated as plain text by the browser. This included special characters 
# like dollar signs, preventing them from being interpreted in ways that could alter their appearance or introduce 
# unwanted formatting.

# Function to wrap text in <pre> tags and escape it
def wrap_in_pre(text):
    # Unescape any previously escaped HTML entities
    text = unescape(text)
    
    # Check if the text is already wrapped in <pre> tags
    if text.startswith('<pre>') and text.endswith('</pre>'):
        return text  # If already wrapped, return as is
    return f"<pre>{html.escape(text)}</pre>" # Wrap in <pre> tags and escape

# Apply the function to your DataFrame column
final_data['scraped_text'] = final_data['scraped_text'].apply(wrap_in_pre)

# Render the DataFrame with the new wrapped text
styled_df = final_data[['original_url', 'scraped_url', 'scraped_text']].style.set_properties(**{
    'text-align': 'left',
    'vertical-align': 'top',
    'white-space': 'normal',
    'font-family': 'Georgia, serif',
    'font-size': '16px',
    'line-height': '1.6',
    'font-weight': 'normal',
    'font-style': 'normal',
    'word-break': 'normal'
}).set_table_styles([
    {'selector': 'th, td',
    'props': [('text-align', 'left'), ('vertical-align', 'top'), ('white-space', 'normal'), ('word-wrap', 'break-word')]},
    {'selector': 'th:nth-child(1), td:nth-child(1)', # Apply styles to the first column
     'props': [('max-width', '120px')]},
    {'selector': 'th:nth-child(2), td:nth-child(2)', # Apply styles to the second column
     'props': [('max-width', '140px')]},
    {'selector': 'th:nth-child(3), td:nth-child(3)', # Apply styles to the third column
     'props': [('max-width', '200px')]}
])

from html import unescape


# Now, strip the inserted <pre> and </pre> tags and unescape HTML entities in case you later need to work with the data
# in its original form. This undoes what wrap_in_pre() did above. This is important because wrap_in_pre() introduced special
# formatting for display purposes.

def strip_pre_tags_and_unescape(text):
    
    # Remove the <pre> and </pre> tags if they exist
    if text.startswith('<pre>') and text.endswith('</pre>'):
        text = text[5:-6]  # Remove the <pre> and </pre> tags
    
    # Unescape any HTML entities in the text
    text = unescape(text)
    
    return text

# Apply the function to your DataFrame column
final_data['scraped_text'] = final_data['scraped_text'].apply(strip_pre_tags_and_unescape)

# Modify the div as follows
html_rendered_dataframe = f"""
<div style='max-height: 400px; overflow-x: auto; overflow-y: auto; border: 1px solid #ccc; padding: 10px; font-family: Georgia, serif; font-size: 16px;'>
    <style>
        table {{
            display: block;
            overflow-x: auto;
            max-width: 100%;
            white-space: nowrap;
        }}
        th, td {{
            font-style: normal !important;
            font-weight: normal !important;
            font-family: Georgia, serif !important;
            font-size: 16px !important;
        }}
    </style>
    {styled_df.to_html(escape=False)}
</div>
"""

# Display the scrollable styled DataFrame
display(HTML(html_rendered_dataframe))


---
---

### **Extract text from a specific scraped web page:**

### Option 1) Using `print()` with `final_data['scraped_text']` and `.iloc[]`. Simply find the index number of the row in the display above that contains your web page of interest, and enter the index number in `.iloc[]`. E.g., if you are interested in viewing the extracted text from Wikipedia's article on "Data Loading" (index 191), located at https://en.wikipedia.org/wiki/Data_loading, you would use the following code:

In [16]:
print(final_data['scraped_text'].iloc[191])

Data loading, or simply loading, is a part of data processing where data is moved between two systems so that it ends up in a staging area on the target system. With the traditional extract, transform and load (ETL) method, the load job is the last step, and the data that is loaded has already been transformed. With the alternative method extract, load and transform (ELT), the loading job is the middle step, and the transformed data is loaded in its original format for data transformation in the target system. Traditionally, loading jobs on large systems have taken a long time, and have typically been run at night outside a company's opening hours. Two main goals of data loading are to obtain fresher data in the systems after loading, and that the loading is fast so that the data can be updated frequently. For full data refresh, faster loading can be achieved by turning off referential integrity, secondary indexes and logging, but this is usually not allowed with incremental update or 

### Option 2) If you want to view the extracted text from your web page of interest (e.g., `.iloc[191]`) with prettier font styling, use the following code which implements the `<pre>` tag and `escape()` steps used earlier:

In [14]:
display(HTML(f"<pre style='font-family: Georgia, serif; font-size: 18px;'>{html.escape(final_data['scraped_text'].iloc[191])}</pre>"))

---
---

### **View Extracted Tables:**

---

### Finally, running the following commented out code will display all tables in HTML scraped from the first 5 web pages (i.e., rows) in the above Pandas DataFrame. I have commented the code out to minimize this HTML document's file size. Simply uncomment the code, and run it.

In [ ]:
"""
from IPython.display import display, HTML

# Use to display tables in html along with their URLs from the first 5 scraped URLs by using .head(). 
for index, row in final_data.head().iterrows():
    # Display the original URL and the scraped URL from which the tables were extracted
    display(HTML(f"<b>Original URL:</b> {row['original_url']}<br><b>Scraped URL:</b> {row['scraped_url']}"))
    
    # Check if there is any HTML table to display
    if row['scraped_tables']:
        display(HTML(row['scraped_tables']))
    else:
        display(HTML("<p>No tables found.</p>"))
    
    # Display a thick black line as a separator after each URL's data before moving on to the next
    if index < len(final_data) - 1:  # Ensure the line is not added after the last item
        display(HTML('<hr style="border: 2px solid black;">'))
        
"""        

### *Note:* If you remove `.head()` from `final_data.head().iterrows()` in the above code, it will show all tables from <u>all scraped URLs</u> (i.e., nearly 700 URLs) saved in the final_data object. However, if you have scraped many URLs as is the case in this portfolio project, doing so will likely overload your memory. 

### In this case, you should instead find the row from the scraped text output from the Pandas DataFrame above that you are interested in viewing (e.g., the Wikipedia website on QVC, located on the row in which index number 58 is displayed on the left-hand side). Then use: final_data.iloc[58] in the following code:

In [3]:
from IPython.display import display, HTML

# Directly access the row in which the index number is 58 (iloc[58]), which shows all extracted tables from 
# the Wikipedia web page on QVC.

row = final_data.iloc[58]

# First display the original URL and the scraped URL from which the tables were extracted
display(HTML(f"<b>Original URL:</b> {row['original_url']}<br><b>Scraped URL:</b> {row['scraped_url']}"))

# Check if there are any HTML tables to display. If so, display them.
if row['scraped_tables']:
    display(HTML(row['scraped_tables']))
else:
    display(HTML("<p>No tables found.</p>"))